# 3-7. 言語・知識 - かな漢字変換

いくつかの文章から単語を分割して取得したい時，同じ意味を持つ単語でも表記が漢字なのかひらがななのかによって別単語と認識してしまうと，想定と違う結果が得られてしまったりする．
そのため，全ての漢字表記をひらがなに変換するなどの処理が行われることがある．実用上ではこれらの処理をどのようにして行っていくのか，ゲームパッケージのタイトルを利用して具体的にみてみよう．

## データの取得・整形
[メディア芸術データベース・ラボ](https://mediag.bunka.go.jp/madb_lab/)上で提供されている[SPARQLクエリサービス](https://mediag.bunka.go.jp/madb_lab/lod/sparql/)を利用して，ゲームパッケージのデータを取得していく．

以下のコードを[SPARQLクエリサービス](https://mediag.bunka.go.jp/madb_lab/lod/sparql/)上に入力して実行する，または入力を省略した[こちらのURL](https://mediag.bunka.go.jp/madb_lab/lod/sparql/#query=PREFIX%20ma%3A%20%3Chttps%3A%2F%2Fmediaarts-db.bunka.go.jp%2Fdata%2Fproperty%23%3E%0APREFIX%20rdfs%3A%20%20%20%3Chttp%3A%2F%2Fwww.w3.org%2F2000%2F01%2Frdf-schema%23%3E%0APREFIX%20schema%3A%20%3Chttps%3A%2F%2Fschema.org%2F%3E%20SELECT%20%3F%E3%83%A9%E3%83%99%E3%83%AB%20%3F%E7%99%BA%E8%A1%8C%E8%80%85%20%3F%E3%83%97%E3%83%A9%E3%83%83%E3%83%88%E3%83%95%E3%82%A9%E3%83%BC%E3%83%A0%20%3F%E3%83%AC%E3%83%BC%E3%83%86%E3%82%A3%E3%83%B3%E3%82%B0%20%3F%E5%85%AC%E9%96%8B%E5%B9%B4%E6%9C%88%E6%97%A5%0AWHERE%20%7B%0A%20%20%3F%E3%82%A2%E3%82%A4%E3%83%86%E3%83%A0%0A%20%20%20%20%20%20%20%20schema%3Agenre%20%22%E3%82%B2%E3%83%BC%E3%83%A0%E3%83%91%E3%83%83%E3%82%B1%E3%83%BC%E3%82%B8%22%3B%0A%20%20%20%20%20%20%20%20schema%3AcontentRating%20%3F%E3%83%AC%E3%83%BC%E3%83%86%E3%82%A3%E3%83%B3%E3%82%B0%3B%0A%20%20%20%20%20%20%20%20schema%3AgamePlatform%20%3F%E3%83%97%E3%83%A9%E3%83%83%E3%83%88%E3%83%95%E3%82%A9%E3%83%BC%E3%83%A0%3B%0A%20%20%20%20%20%20%20%20schema%3Apublisher%20%3F%E7%99%BA%E8%A1%8C%E8%80%85%3B%0A%20%20%20%20%20%20%20%20rdfs%3Alabel%20%3F%E3%83%A9%E3%83%99%E3%83%AB%3B%0A%20%20%20%20%20%20%20%20ma%3AdatePublished%20%3F%E5%85%AC%E9%96%8B%E5%B9%B4%E6%9C%88%E6%97%A5.%0A%7D&endpoint=https%3A%2F%2Fmediag.bunka.go.jp%2Fsparql&requestMethod=POST&tabTitle=Query&headers=%7B%7D&contentTypeConstruct=application%2Fn-triples%2C*%2F*%3Bq%3D0.9&contentTypeSelect=application%2Fsparql-results%2Bjson%2C*%2F*%3Bq%3D0.9&outputFormat=table)から実行してデータを取得できる．
取得したCSVファイルを「ゲームパッケージ.csv」として保存し，このノートブック上にアップロードしよう．

※「3-4. ディープニューラルネットワーク（DNN）」，「3-4. 学習用データと学習済みモデル」，「3-6. 決定木」，「3-6. サポートベクターマシン」，「3-7. 形態素解析」，「3-7. 表現学習」と同じデータセットを作成するため，もし同じものを持っている場合は以下の取得作業は不要なので，そちらをアップロードしよう．

```
PREFIX ma: <https://mediaarts-db.bunka.go.jp/data/property#>
PREFIX rdfs:   <http://www.w3.org/2000/01/rdf-schema#>
PREFIX schema: <https://schema.org/> SELECT ?ラベル ?発行者 ?プラットフォーム ?レーティング ?公開年月日
WHERE {
  ?アイテム
        schema:genre "ゲームパッケージ";
        schema:contentRating ?レーティング;
        schema:gamePlatform ?プラットフォーム;
        schema:publisher ?発行者;
        rdfs:label ?ラベル;
        ma:datePublished ?公開年月日.
}
```

取得したデータセットを，Python上で扱いやすい形にしていく．
pandasというライブラリを用いて，csv形式のファイルの中身をDataFrameという型に変換し，扱っていく．

In [8]:
# 必要なモジュールのインポート
!pip install pykakasi
import pykakasi
import pandas as pd
import collections

In [9]:
games = pd.read_csv("/content/ゲームパッケージ.csv")
games = games.drop_duplicates(subset='ラベル')
games = games.reset_index(drop=True)
games

ラベル  \
0                           Dance Dance Revolution GB2   
1                                     プロ野球 ファミスタ リターンズ   
2                                      プロ野球 ファミスタ 2011   
3                                              フロッガー3D   
4                                           ブレイブリーセカンド   
...                                                ...   
19452                 バイオショック インフィニット PlayStation Now版   
19453  バイオハザード リベレーションズ アンベールド エディション PlayStation Now版   
19454                           巫剣神威控 PlayStation Now版   
19455                 ネバーエンディング ナイトメア PlayStation Now版   
19456                   雷電IV OverKill PlayStation Now版   

                           発行者       プラットフォーム            レーティング       公開年月日  
0                      コナミ株式会社         ゲームボーイ  CERO D (17才以上対象)  2000-11-16  
1        株式会社バンダイナムコエンターテインメント      ニンテンドー3DS    CERO A (全年齢対象)  2015-10-08  
2              株式会社バンダイナムコゲームス      ニンテンドー3DS    CERO A (全年齢対象)  2011-03-31  
3         株式会社コナミデジタルエンタテインメント      ニンテンドー3DS    CERO A (全年齢対象)  2011-09-22  
4              株式会社スクウェア・エニックス      ニンテンドー3DS  CERO C (15才以上対象)  2015-04-23  
...                        ...            ...               ...         ...  
19452  テイクツー・インタラクティブ・ジャパン合同会社  プレイステーション Now  CERO D (17才以上対象)  2017-09-19  
19453                 株式会社カプコン  プレイステーション Now  CERO D (17才以上対象)  2016-09-20  
19454           アクティブゲーミングメディア  プレイステーション Now  CERO C (15才以上対象)  2017-07-20  
19455           アクティブゲーミングメディア  プレイステーション Now  CERO D (17才以上対象)  2017-07-20  
19456                       モス  プレイステーション Now    CERO A (全年齢対象)  2017-02-21  

[19457 rows x 5 columns]

## かな漢字変換
今回はkakasiというモジュールを利用する．

In [10]:
# kakasiのインスタンスを作成
kks = pykakasi.kakasi()

# 変換
result = kks.convert(games['ラベル'][0])
print(result)

[{'orig': 'Dance Dance Revolution GB2', 'hira': 'Dance Dance Revolution GB2', 'kana': 'Dance Dance Revolution GB2', 'hepburn': 'Dance Dance Revolution GB2', 'kunrei': 'Dance Dance Revolution GB2', 'passport': 'Dance Dance Revolution GB2'}]


上のように，オリジナルの文字列からひらがな・カタカナ・ローマ字などへの変換結果が出ている．
もしひらがなの変換結果のみを受け取りたい場合は，次のように`'hira'`を指定して取得する．

In [11]:
for token in result:
  print(token['hira'])

Dance Dance Revolution GB2


In [12]:
# 全データに対してかな漢字変換を行ってみる

# ひらがなのデータを入れる
title_hira = []
# オリジナルのデータを入れる
title_origin = []

for title in games['ラベル']:
  title_hira.extend([token["hira"] for token in kks.convert(title)])
  title_origin.extend([token["orig"] for token in kks.convert(title)])

この結果，出てくる単語の頻度がどのように変化するのか確認してみよう．

In [13]:
count_hira = collections.Counter(title_hira)
count_origin = collections.Counter(title_origin)

print(f"ひらがなに変換した後の「さくら」の登場回数: {count_hira['さくら']}")
print(f"オリジナルの「さくら」の登場回数: {count_origin['さくら']}")
print(f"オリジナルの「サクラ」の登場回数: {count_origin['サクラ']}")
print(f"オリジナルの「桜」の登場回数: {count_origin['桜']}")

ひらがなに変換した後の「さくら」の登場回数: 123
オリジナルの「さくら」の登場回数: 8
オリジナルの「サクラ」の登場回数: 36
オリジナルの「桜」の登場回数: 79


このように表記の異なるものについても同じように集計することができる．
しかし，同音異義語についても同じように集計されてしまうため，注意が必要である．

In [14]:
print(f"ひらがなに変換した後の「じゅう」の登場回数: {count_hira['じゅう']}")
print(f"オリジナルの「銃」の登場回数: {count_origin['銃']}")
print(f"オリジナルの「十」の登場回数: {count_origin['十']}")
print(f"オリジナルの「重」の登場回数: {count_origin['重']}")


ひらがなに変換した後の「じゅう」の登場回数: 11
オリジナルの「銃」の登場回数: 1
オリジナルの「十」の登場回数: 6
オリジナルの「重」の登場回数: 4
